# A ML Regression analysis for Airbnb prices in New_Brunswhick, Canada

# Step 1: Clean Up

In [0]:
# This data comes from http://insideairbnb.com/get-the-data.html, and comes from the New Brunswick, Canada 2021 dataset
nb = spark.table("default.nb_airibnb_listings_gz") # came from renamed ".gz" file I renamed "nb_airbnb_lisitngs"
display(nb)

id listing_url scrape_id last_scraped name description neighborhood_overview picture_url host_id host_url host_name host_since host_location host_about host_response_time host_response_rate host_acceptance_rate host_is_superhost host_thumbnail_url host_picture_url host_neighbourhood host_listings_count host_total_listings_count host_verifications host_has_profile_pic host_identity_verified neighbourhood neighbourhood_cleansed neighbourhood_group_cleansed latitude longitude property_type room_type accommodates bathrooms bathrooms_text bedrooms beds amenities price minimum_nights maximum_nights minimum_minimum_nights maximum_minimum_nights minimum_maximum_nights maximum_maximum_nights minimum_nights_avg_ntm maximum_nights_avg_ntm calendar_updated has_availability availability_30 availability_60 availability_90 availability_365 calendar_last_scraped number_of_reviews number_of_reviews_ltm number_of_reviews_l30d first_review last_review review_scores_rating review_scores_accuracy review_scores_cleanliness review_scores_checkin review_scores_communication review_scores_location review_scores_value license instant_bookable calculated_host_listings_count calculated_host_listings_count_entire_homes calculated_host_listings_count_private_rooms calculated_host_listings_count_shared_rooms reviews_per_month 75065 https://www.airbnb.com/rooms/75065 20210720033223 2021-07-20 Bay cottage on Passamaquoddy bay The space This beautiful two bedroom getaway cottage is nestled on a one acre oceanfront secluded vacation spot. With over 450' of bluffed shoreline along its flanks, it presents a spectacular view of Passamaquoddy Bay. The tourist town of St. Andrews by the Sea is just miles away. The cozy cottage presents an open floor concept with a front view to the ocean with two bedrooms and a modern kitchen. A wrap around deck provides a vantage point for relaxing and taking in the scenery. There is an access to the beach where a sitting and fire pit area are carved out of the rocks just feet from the tide line. There is also over a mile of shoreline to stroll on for those who love beach-combing. If you love the outdoors, oceanfront scenery and a friendly atmosphere, give us a call. null https://a0.muscache.com/pictures/16035357/d70d8cb2_original.jpg 397069 https://www.airbnb.com/users/show/397069 Bob 2011-02-17 Spring, Texas, United States This property is our final resting place and retirement home someday. We were raised nearby and have spent a lot of time in the St. Andrews area. We love the scenery and friendly atmosphere of the area. within a few hours 100% 100% f https://a0.muscache.com/im/users/397069/profile_pic/1297982992/original.jpg?aki_policy=profile_small https://a0.muscache.com/im/users/397069/profile_pic/1297982992/original.jpg?aki_policy=profile_x_medium null 1 1 ['email', 'phone', 'reviews', 'jumio', 'government_id'] t t null Saint Andrews Charlotte 45.13241 -67.04725 Entire house Entire home/apt 6 null 1 bath 2 5 ["Cooking basics", "TV", "Lockbox", "Washer", "Kitchen", "Indoor fireplace", "Free parking on premises", "Wifi", "Heating", "Long term stays allowed", "Hot water", "Dryer", "Dishes and silverware"] $242.00 2 730 2 2 1125 1125 2.0 1125.0 null t 5 16 40 315 2021-07-20 21 6 3 2019-10-13 2019-10-20 4.67 4.71 4.57 5.0 4.86 4.9 4.62 null f 1 1 0 0 0.97 145013 https://www.airbnb.com/rooms/145013 20210720033223 2021-07-20 Lobster Lane Cottage: private beach This cottage rents Sunday to Sunday in high season. Enjoy fresh seafood and bonfires at night while you experience Atlantic Canada! This cottage is nicely appointed with all you will need during your stay. If you are looking for a quiet summer holiday with a warm, sandy beach this is it! Caissie Cape is well known to locals to have one of the loveliest beaches in Southeast New Brunswick. The neighbours are delightfully friendly and you will love the environment. The space Reservations are now being taken for Summer 2019! Weekly rentals are from Sunday (check-in 4pm) to Sunda

let's do some quick data cleanup before saving it into the Delta Lake

In [0]:
# Selecting relevent columns

columnsToKeep = [
  "host_is_superhost",
  "host_response_time",
  "host_response_rate",
  "host_acceptance_rate",
  "host_total_listings_count",
  "neighbourhood_cleansed",
  "latitude",
  "longitude",
  "room_type",
  "accommodates",
  "bathrooms_text",
  "bedrooms",
  "beds",
  "minimum_nights",
  "availability_30",
  "availability_60",
  "availability_90",
  "availability_365",
  "number_of_reviews",
  "review_scores_rating",
  "review_scores_accuracy",
  "review_scores_cleanliness",
  "review_scores_checkin",
  "review_scores_communication",
  "review_scores_location",
  "review_scores_value",
  "reviews_per_month", 
  "price"]
baseDF = nb.select(columnsToKeep)
baseDF.cache().count()
display(baseDF)

#price is my target featuer, I will be trying to predict the nightly price of air bnb

host_is_superhost host_response_time host_response_rate host_acceptance_rate host_total_listings_count neighbourhood_cleansed latitude longitude room_type accommodates bathrooms_text bedrooms beds minimum_nights availability_30 availability_60 availability_90 availability_365 number_of_reviews review_scores_rating review_scores_accuracy review_scores_cleanliness review_scores_checkin review_scores_communication review_scores_location review_scores_value reviews_per_month price f within a few hours 100% 100% 1 Saint Andrews 45.13241 -67.04725 Entire home/apt 6 1 bath 2 5 2 5 16 40 315 21 4.67 4.71 4.57 5.0 4.86 4.9 4.62 0.97 $242.00 f within a day 100% 33% 1 Dundas 46.32857 -64.52445 Entire home/apt 5 1 bath 3 3 7 0 0 17 292 8 5.0 4.88 5.0 4.86 4.71 5.0 4.71 0.11 $125.00 f within a few hours 100% 100% 2 City of Saint John 45.27727 -66.0604 Entire home/apt 4 1 bath 2 5 2 0 0 17 292 44 4.59 4.68 4.77 4.68 4.84 4.68 4.73 1.27 $103.00 f within a few hours 100% 67% 1 Sackville 45.894821 -64.376556 Private room 2 1 private bath 1 1 1 2 5 26 275 52 4.77 4.9 4.81 4.88 4.92 4.92 4.82 0.53 $69.00 f N/A N/A 0% 1 Shippagan 47.86785 -64.52187 Entire home/apt 6 1.5 baths 2 2 7 0 0 0 261 3 4.67 3.67 4.67 4.67 4.67 4.67 4.33 0.13 $135.00 f within a day 67% N/A 1 Cambridge 45.85825 -66.11696 Entire home/apt 2 1 bath 2 1 7 23 53 83 358 0 null null null null null null null null $130.00 t within an hour 100% 97% 3 Moncton 46.10555 -64.81432 Entire home/apt 7 1 bath 3 4 3 7 22 49 323 192 4.88 4.92 4.86 4.94 4.95 4.79 4.86 2.27 $138.00 f within a day 100% 100% 8 City of Saint John 45.27233 -66.05694 Private room 2 1 private bath 1 1 1 25 55 85 360 126 4.58 4.63 4.83 4.65 4.67 4.67 4.64 1.71 $145.00 f within a day 100% 100% 0 Gagetown 45.78008 -66.14374 Entire home/apt 2 1 bath 1 1 2 17 47 77 77 1 5.0 5.0 5.0 5.0 5.0 5.0 5.0 1.0 $215.00 t within a day 95% 83% 10 City of Saint John 45.27358 -66.05307 Private room 2 1 private bath 1 1 1 0 0 0 80 39 4.84 4.95 4.79 4.89 4.92 4.82 4.84 0.54 $125.00 t within an hour 100% 100% 1 Bright 45.97722 -66.84614 Entire home/apt 4 1 bath 2 3 3 0 8 19 283 134 4.72 4.89 4.92 4.91 4.92 4.62 4.78 1.82 $139.00 f within a day 100% 100% 8 City of Saint John 45.27406 -66.05772 Private room 2 1 private bath null 1 1 26 56 86 361 70 4.71 4.78 4.81 4.88 4.86 4.81 4.76 1.41 $159.00 f within a few hours 100% 95% 4 Springfield 45.64933 -65.8593 Private room 16 3.5 shared baths 9 10 1 10 28 55 330 63 4.7 4.82 4.69 4.89 4.92 4.73 4.82 1.04 $35.00 f N/A N/A N/A 1 Richibucto 46.68234 -64.80627 Entire home/apt 5 1 bath 2 3 2 1 18 48 173 103 4.76 4.86 4.45 4.96 4.97 4.84 4.72 1.41 $150.00 f within a few hours 100% 95% 4 Springfield 45.64943 -65.86004 Private room 16 3.5 shared baths 9 9 1 10 28 55 330 131 4.71 4.85 4.66 4.86 4.88 4.7 4.81 1.55 $35.00 f N/A N/A 67% 1 Kingston 45.44755 -66.00487 Entire home/apt 8 1 bath 4 5 7 1 1 1 1 44 4.45 4.62 4.42 4.77 4.59 4.84 4.48 0.91 $150.00 t N/A N/A 100% 3 Hillsborough 45.94133 -64.66544 Entire home/apt 2 1 bath 1 1 2 0 17 47 322 49 4.96 4.94 5.0 4.98 4.91 4.84 4.88 1.01 $150.00 f within a few hours 100% 83% 1 Alnwick 47.1967 -65.14315 Entire home/apt 2 1 bath 1 2 3 0 6 36 311 57 4.84 4.93 4.89 4.96 4.95 4.77 4.95 0.94 $60.00 t within a day 95% 83% 10 City of Saint John 45.27354 -66.05299 Private room 2 1 private bath 1 0 1 0 0 0 80 50 4.8 4.88 4.88 4.98 4.96 4.78 4.82 0.66 $160.00 f a few days or more 42% 38% 0 Saint George 45.0635 -66.82176 Entire home/apt 5 1 bath 3 3 2 0 13 43 312 184 4.91 4.93 4.93 4.87 4.8 4.93 4.91 2.12 $130.00 t within an hour 100% 100% 4 Fredericton 45.95817 -66.63426 Entire home/apt 2 1 bath 1 1 1 0 9 29 304 299 4.8 4.9 4.88 4.95 4.92 4.98 4.77 3.52 $142.00 t within an hour 100% 96% 2 Saint Andrews 45.0754 -67.05535 Entire home/apt 4 1 bath 1 2 2 1 1 1 76 46 4.91 4.84 4.89 4.89 4.87 4.98 4.82 1.29 $147.00 t within an hour 100% 86% 2 Fredericton 45.93823 -66.64044 Private room 2 1.5 shared baths 1 0 1 13 34 64 339 75 4.97 4.92 4.92 4.93 4.95 4.83 4.86 1.57 $100.00 t w

In [0]:
## price is listed as a string and has a dollar sign, so lets fix that
from pyspark.sql.functions import col, translate



fixedPriceDF = baseDF.withColumn("price", translate(col("price"), "$,", "").cast("double")) 
# with column will overwrite my price column and will replace $ and comma's with an empty space and then will save it as a double 
display(fixedPriceDF)

host_is_superhost host_response_time host_response_rate host_acceptance_rate host_total_listings_count neighbourhood_cleansed latitude longitude room_type accommodates bathrooms_text bedrooms beds minimum_nights availability_30 availability_60 availability_90 availability_365 number_of_reviews review_scores_rating review_scores_accuracy review_scores_cleanliness review_scores_checkin review_scores_communication review_scores_location review_scores_value reviews_per_month price f within a few hours 100% 100% 1 Saint Andrews 45.13241 -67.04725 Entire home/apt 6 1 bath 2 5 2 5 16 40 315 21 4.67 4.71 4.57 5.0 4.86 4.9 4.62 0.97 242.0 f within a day 100% 33% 1 Dundas 46.32857 -64.52445 Entire home/apt 5 1 bath 3 3 7 0 0 17 292 8 5.0 4.88 5.0 4.86 4.71 5.0 4.71 0.11 125.0 f within a few hours 100% 100% 2 City of Saint John 45.27727 -66.0604 Entire home/apt 4 1 bath 2 5 2 0 0 17 292 44 4.59 4.68 4.77 4.68 4.84 4.68 4.73 1.27 103.0 f within a few hours 100% 67% 1 Sackville 45.894821 -64.376556 Private room 2 1 private bath 1 1 1 2 5 26 275 52 4.77 4.9 4.81 4.88 4.92 4.92 4.82 0.53 69.0 f N/A N/A 0% 1 Shippagan 47.86785 -64.52187 Entire home/apt 6 1.5 baths 2 2 7 0 0 0 261 3 4.67 3.67 4.67 4.67 4.67 4.67 4.33 0.13 135.0 f within a day 67% N/A 1 Cambridge 45.85825 -66.11696 Entire home/apt 2 1 bath 2 1 7 23 53 83 358 0 null null null null null null null null 130.0 t within an hour 100% 97% 3 Moncton 46.10555 -64.81432 Entire home/apt 7 1 bath 3 4 3 7 22 49 323 192 4.88 4.92 4.86 4.94 4.95 4.79 4.86 2.27 138.0 f within a day 100% 100% 8 City of Saint John 45.27233 -66.05694 Private room 2 1 private bath 1 1 1 25 55 85 360 126 4.58 4.63 4.83 4.65 4.67 4.67 4.64 1.71 145.0 f within a day 100% 100% 0 Gagetown 45.78008 -66.14374 Entire home/apt 2 1 bath 1 1 2 17 47 77 77 1 5.0 5.0 5.0 5.0 5.0 5.0 5.0 1.0 215.0 t within a day 95% 83% 10 City of Saint John 45.27358 -66.05307 Private room 2 1 private bath 1 1 1 0 0 0 80 39 4.84 4.95 4.79 4.89 4.92 4.82 4.84 0.54 125.0 t within an hour 100% 100% 1 Bright 45.97722 -66.84614 Entire home/apt 4 1 bath 2 3 3 0 8 19 283 134 4.72 4.89 4.92 4.91 4.92 4.62 4.78 1.82 139.0 f within a day 100% 100% 8 City of Saint John 45.27406 -66.05772 Private room 2 1 private bath null 1 1 26 56 86 361 70 4.71 4.78 4.81 4.88 4.86 4.81 4.76 1.41 159.0 f within a few hours 100% 95% 4 Springfield 45.64933 -65.8593 Private room 16 3.5 shared baths 9 10 1 10 28 55 330 63 4.7 4.82 4.69 4.89 4.92 4.73 4.82 1.04 35.0 f N/A N/A N/A 1 Richibucto 46.68234 -64.80627 Entire home/apt 5 1 bath 2 3 2 1 18 48 173 103 4.76 4.86 4.45 4.96 4.97 4.84 4.72 1.41 150.0 f within a few hours 100% 95% 4 Springfield 45.64943 -65.86004 Private room 16 3.5 shared baths 9 9 1 10 28 55 330 131 4.71 4.85 4.66 4.86 4.88 4.7 4.81 1.55 35.0 f N/A N/A 67% 1 Kingston 45.44755 -66.00487 Entire home/apt 8 1 bath 4 5 7 1 1 1 1 44 4.45 4.62 4.42 4.77 4.59 4.84 4.48 0.91 150.0 t N/A N/A 100% 3 Hillsborough 45.94133 -64.66544 Entire home/apt 2 1 bath 1 1 2 0 17 47 322 49 4.96 4.94 5.0 4.98 4.91 4.84 4.88 1.01 150.0 f within a few hours 100% 83% 1 Alnwick 47.1967 -65.14315 Entire home/apt 2 1 bath 1 2 3 0 6 36 311 57 4.84 4.93 4.89 4.96 4.95 4.77 4.95 0.94 60.0 t within a day 95% 83% 10 City of Saint John 45.27354 -66.05299 Private room 2 1 private bath 1 0 1 0 0 0 80 50 4.8 4.88 4.88 4.98 4.96 4.78 4.82 0.66 160.0 f a few days or more 42% 38% 0 Saint George 45.0635 -66.82176 Entire home/apt 5 1 bath 3 3 2 0 13 43 312 184 4.91 4.93 4.93 4.87 4.8 4.93 4.91 2.12 130.0 t within an hour 100% 100% 4 Fredericton 45.95817 -66.63426 Entire home/apt 2 1 bath 1 1 1 0 9 29 304 299 4.8 4.9 4.88 4.95 4.92 4.98 4.77 3.52 142.0 t within an hour 100% 96% 2 Saint Andrews 45.0754 -67.05535 Entire home/apt 4 1 bath 1 2 2 1 1 1 76 46 4.91 4.84 4.89 4.89 4.87 4.98 4.82 1.29 147.0 t within an hour 100% 86% 2 Fredericton 45.93823 -66.64044 Private room 2 1.5 shared baths 1 0 1 13 34 64 339 75 4.97 4.92 4.92 4.93 4.95 4.83 4.86 1.57 100.0 t within an hour 100% 61% 2 Shediac 46.23471 -64.

In [0]:
# lets split the bathrooms_text column so we only keep the integer before the strings
import pyspark
from pyspark.sql.types import DoubleType

split_col = pyspark.sql.functions.split(fixedPriceDF['bathrooms_text'], ' ') 
fixedPriceDF = fixedPriceDF.withColumn('bathrooms', split_col.getItem(0).cast(DoubleType())).drop(col("bathrooms_text"))

display(fixedPriceDF)

host_is_superhost host_response_time host_response_rate host_acceptance_rate host_total_listings_count neighbourhood_cleansed latitude longitude room_type accommodates bedrooms beds minimum_nights availability_30 availability_60 availability_90 availability_365 number_of_reviews review_scores_rating review_scores_accuracy review_scores_cleanliness review_scores_checkin review_scores_communication review_scores_location review_scores_value reviews_per_month price bathrooms f within a few hours 100% 100% 1 Saint Andrews 45.13241 -67.04725 Entire home/apt 6 2 5 2 5 16 40 315 21 4.67 4.71 4.57 5.0 4.86 4.9 4.62 0.97 242.0 1.0 f within a day 100% 33% 1 Dundas 46.32857 -64.52445 Entire home/apt 5 3 3 7 0 0 17 292 8 5.0 4.88 5.0 4.86 4.71 5.0 4.71 0.11 125.0 1.0 f within a few hours 100% 100% 2 City of Saint John 45.27727 -66.0604 Entire home/apt 4 2 5 2 0 0 17 292 44 4.59 4.68 4.77 4.68 4.84 4.68 4.73 1.27 103.0 1.0 f within a few hours 100% 67% 1 Sackville 45.894821 -64.376556 Private room 2 1 1 1 2 5 26 275 52 4.77 4.9 4.81 4.88 4.92 4.92 4.82 0.53 69.0 1.0 f N/A N/A 0% 1 Shippagan 47.86785 -64.52187 Entire home/apt 6 2 2 7 0 0 0 261 3 4.67 3.67 4.67 4.67 4.67 4.67 4.33 0.13 135.0 1.5 f within a day 67% N/A 1 Cambridge 45.85825 -66.11696 Entire home/apt 2 2 1 7 23 53 83 358 0 null null null null null null null null 130.0 1.0 t within an hour 100% 97% 3 Moncton 46.10555 -64.81432 Entire home/apt 7 3 4 3 7 22 49 323 192 4.88 4.92 4.86 4.94 4.95 4.79 4.86 2.27 138.0 1.0 f within a day 100% 100% 8 City of Saint John 45.27233 -66.05694 Private room 2 1 1 1 25 55 85 360 126 4.58 4.63 4.83 4.65 4.67 4.67 4.64 1.71 145.0 1.0 f within a day 100% 100% 0 Gagetown 45.78008 -66.14374 Entire home/apt 2 1 1 2 17 47 77 77 1 5.0 5.0 5.0 5.0 5.0 5.0 5.0 1.0 215.0 1.0 t within a day 95% 83% 10 City of Saint John 45.27358 -66.05307 Private room 2 1 1 1 0 0 0 80 39 4.84 4.95 4.79 4.89 4.92 4.82 4.84 0.54 125.0 1.0 t within an hour 100% 100% 1 Bright 45.97722 -66.84614 Entire home/apt 4 2 3 3 0 8 19 283 134 4.72 4.89 4.92 4.91 4.92 4.62 4.78 1.82 139.0 1.0 f within a day 100% 100% 8 City of Saint John 45.27406 -66.05772 Private room 2 null 1 1 26 56 86 361 70 4.71 4.78 4.81 4.88 4.86 4.81 4.76 1.41 159.0 1.0 f within a few hours 100% 95% 4 Springfield 45.64933 -65.8593 Private room 16 9 10 1 10 28 55 330 63 4.7 4.82 4.69 4.89 4.92 4.73 4.82 1.04 35.0 3.5 f N/A N/A N/A 1 Richibucto 46.68234 -64.80627 Entire home/apt 5 2 3 2 1 18 48 173 103 4.76 4.86 4.45 4.96 4.97 4.84 4.72 1.41 150.0 1.0 f within a few hours 100% 95% 4 Springfield 45.64943 -65.86004 Private room 16 9 9 1 10 28 55 330 131 4.71 4.85 4.66 4.86 4.88 4.7 4.81 1.55 35.0 3.5 f N/A N/A 67% 1 Kingston 45.44755 -66.00487 Entire home/apt 8 4 5 7 1 1 1 1 44 4.45 4.62 4.42 4.77 4.59 4.84 4.48 0.91 150.0 1.0 t N/A N/A 100% 3 Hillsborough 45.94133 -64.66544 Entire home/apt 2 1 1 2 0 17 47 322 49 4.96 4.94 5.0 4.98 4.91 4.84 4.88 1.01 150.0 1.0 f within a few hours 100% 83% 1 Alnwick 47.1967 -65.14315 Entire home/apt 2 1 2 3 0 6 36 311 57 4.84 4.93 4.89 4.96 4.95 4.77 4.95 0.94 60.0 1.0 t within a day 95% 83% 10 City of Saint John 45.27354 -66.05299 Private room 2 1 0 1 0 0 0 80 50 4.8 4.88 4.88 4.98 4.96 4.78 4.82 0.66 160.0 1.0 f a few days or more 42% 38% 0 Saint George 45.0635 -66.82176 Entire home/apt 5 3 3 2 0 13 43 312 184 4.91 4.93 4.93 4.87 4.8 4.93 4.91 2.12 130.0 1.0 t within an hour 100% 100% 4 Fredericton 45.95817 -66.63426 Entire home/apt 2 1 1 1 0 9 29 304 299 4.8 4.9 4.88 4.95 4.92 4.98 4.77 3.52 142.0 1.0 t within an hour 100% 96% 2 Saint Andrews 45.0754 -67.05535 Entire home/apt 4 1 2 2 1 1 1 76 46 4.91 4.84 4.89 4.89 4.87 4.98 4.82 1.29 147.0 1.0 t within an hour 100% 86% 2 Fredericton 45.93823 -66.64044 Private room 2 1 0 1 13 34 64 339 75 4.97 4.92 4.92 4.93 4.95 4.83 4.86 1.57 100.0 1.5 t within an hour 100% 61% 2 Shediac 46.23471 -64.51617 Entire home/apt 8 4 5 7 0 11 41 316 36 4.5 4.66 4.33 4.86 4.89 4.91 4.46 0.49 235.0 1.0 f N/A N/A N/A 2 Wellington 46.47954 -64.69794 Private

In [0]:
# need to fix columns "host_response_rate" and "host_acceptance_rate" to integer columns with percentages



split_col2 = pyspark.sql.functions.split(fixedPriceDF['host_response_rate'], '%') 
fixedPriceDF = fixedPriceDF.withColumn('host_response_rate', (split_col2.getItem(0).cast(DoubleType())) / 100)

split_col3 = pyspark.sql.functions.split(fixedPriceDF['host_acceptance_rate'], '%') 
fixedPriceDF = fixedPriceDF.withColumn('host_acceptance_rate', (split_col3.getItem(0).cast(DoubleType())) / 100)

display(fixedPriceDF)

host_is_superhost host_response_time host_response_rate host_acceptance_rate host_total_listings_count neighbourhood_cleansed latitude longitude room_type accommodates bedrooms beds minimum_nights availability_30 availability_60 availability_90 availability_365 number_of_reviews review_scores_rating review_scores_accuracy review_scores_cleanliness review_scores_checkin review_scores_communication review_scores_location review_scores_value reviews_per_month price bathrooms f within a few hours 1.0 1.0 1 Saint Andrews 45.13241 -67.04725 Entire home/apt 6 2 5 2 5 16 40 315 21 4.67 4.71 4.57 5.0 4.86 4.9 4.62 0.97 242.0 1.0 f within a day 1.0 0.33 1 Dundas 46.32857 -64.52445 Entire home/apt 5 3 3 7 0 0 17 292 8 5.0 4.88 5.0 4.86 4.71 5.0 4.71 0.11 125.0 1.0 f within a few hours 1.0 1.0 2 City of Saint John 45.27727 -66.0604 Entire home/apt 4 2 5 2 0 0 17 292 44 4.59 4.68 4.77 4.68 4.84 4.68 4.73 1.27 103.0 1.0 f within a few hours 1.0 0.67 1 Sackville 45.894821 -64.376556 Private room 2 1 1 1 2 5 26 275 52 4.77 4.9 4.81 4.88 4.92 4.92 4.82 0.53 69.0 1.0 f N/A null 0.0 1 Shippagan 47.86785 -64.52187 Entire home/apt 6 2 2 7 0 0 0 261 3 4.67 3.67 4.67 4.67 4.67 4.67 4.33 0.13 135.0 1.5 f within a day 0.67 null 1 Cambridge 45.85825 -66.11696 Entire home/apt 2 2 1 7 23 53 83 358 0 null null null null null null null null 130.0 1.0 t within an hour 1.0 0.97 3 Moncton 46.10555 -64.81432 Entire home/apt 7 3 4 3 7 22 49 323 192 4.88 4.92 4.86 4.94 4.95 4.79 4.86 2.27 138.0 1.0 f within a day 1.0 1.0 8 City of Saint John 45.27233 -66.05694 Private room 2 1 1 1 25 55 85 360 126 4.58 4.63 4.83 4.65 4.67 4.67 4.64 1.71 145.0 1.0 f within a day 1.0 1.0 0 Gagetown 45.78008 -66.14374 Entire home/apt 2 1 1 2 17 47 77 77 1 5.0 5.0 5.0 5.0 5.0 5.0 5.0 1.0 215.0 1.0 t within a day 0.95 0.83 10 City of Saint John 45.27358 -66.05307 Private room 2 1 1 1 0 0 0 80 39 4.84 4.95 4.79 4.89 4.92 4.82 4.84 0.54 125.0 1.0 t within an hour 1.0 1.0 1 Bright 45.97722 -66.84614 Entire home/apt 4 2 3 3 0 8 19 283 134 4.72 4.89 4.92 4.91 4.92 4.62 4.78 1.82 139.0 1.0 f within a day 1.0 1.0 8 City of Saint John 45.27406 -66.05772 Private room 2 null 1 1 26 56 86 361 70 4.71 4.78 4.81 4.88 4.86 4.81 4.76 1.41 159.0 1.0 f within a few hours 1.0 0.95 4 Springfield 45.64933 -65.8593 Private room 16 9 10 1 10 28 55 330 63 4.7 4.82 4.69 4.89 4.92 4.73 4.82 1.04 35.0 3.5 f N/A null null 1 Richibucto 46.68234 -64.80627 Entire home/apt 5 2 3 2 1 18 48 173 103 4.76 4.86 4.45 4.96 4.97 4.84 4.72 1.41 150.0 1.0 f within a few hours 1.0 0.95 4 Springfield 45.64943 -65.86004 Private room 16 9 9 1 10 28 55 330 131 4.71 4.85 4.66 4.86 4.88 4.7 4.81 1.55 35.0 3.5 f N/A null 0.67 1 Kingston 45.44755 -66.00487 Entire home/apt 8 4 5 7 1 1 1 1 44 4.45 4.62 4.42 4.77 4.59 4.84 4.48 0.91 150.0 1.0 t N/A null 1.0 3 Hillsborough 45.94133 -64.66544 Entire home/apt 2 1 1 2 0 17 47 322 49 4.96 4.94 5.0 4.98 4.91 4.84 4.88 1.01 150.0 1.0 f within a few hours 1.0 0.83 1 Alnwick 47.1967 -65.14315 Entire home/apt 2 1 2 3 0 6 36 311 57 4.84 4.93 4.89 4.96 4.95 4.77 4.95 0.94 60.0 1.0 t within a day 0.95 0.83 10 City of Saint John 45.27354 -66.05299 Private room 2 1 0 1 0 0 0 80 50 4.8 4.88 4.88 4.98 4.96 4.78 4.82 0.66 160.0 1.0 f a few days or more 0.42 0.38 0 Saint George 45.0635 -66.82176 Entire home/apt 5 3 3 2 0 13 43 312 184 4.91 4.93 4.93 4.87 4.8 4.93 4.91 2.12 130.0 1.0 t within an hour 1.0 1.0 4 Fredericton 45.95817 -66.63426 Entire home/apt 2 1 1 1 0 9 29 304 299 4.8 4.9 4.88 4.95 4.92 4.98 4.77 3.52 142.0 1.0 t within an hour 1.0 0.96 2 Saint Andrews 45.0754 -67.05535 Entire home/apt 4 1 2 2 1 1 1 76 46 4.91 4.84 4.89 4.89 4.87 4.98 4.82 1.29 147.0 1.0 t within an hour 1.0 0.86 2 Fredericton 45.93823 -66.64044 Private room 2 1 0 1 13 34 64 339 75 4.97 4.92 4.92 4.93 4.95 4.83 4.86 1.57 100.0 1.5 t within an hour 1.0 0.61 2 Shediac 46.23471 -64.51617 Entire home/apt 8 4 5 7 0 11 41 316 36 4.5 4.66 4.33 4.86 4.89 4.91 4.46 0.49 235.0 1.0 f N/A null null 2 Wellington 46.47954 -64.69794 Priva

In [0]:

# SparkML Imputer requires all integer columns to be doubles

from pyspark.sql.functions import col
from pyspark.sql.types import IntegerType

integerColumns = [x.name for x in fixedPriceDF.schema.fields if x.dataType == IntegerType()]
doublesDF = fixedPriceDF

for c in integerColumns:
  doublesDF = doublesDF.withColumn(c, col(c).cast("double"))

columns = "\n - ".join(integerColumns)
print(f"Columns converted from Integer to Double:\n - {columns}")

Columns converted from Integer to Double:
 - host_total_listings_count
 - accommodates
 - bedrooms
 - beds
 - minimum_nights
 - availability_30
 - availability_60
 - availability_90
 - availability_365
 - number_of_reviews

In [0]:
from pyspark.sql.functions import when

############ I need to figure out what to do with the response rate columns with null values #####

# 

imputeCols = [
  "bedrooms",
  "bathrooms",
  "beds", 
  "review_scores_rating",
  "review_scores_accuracy",
  "review_scores_cleanliness",
  "review_scores_checkin",
  "review_scores_communication",
  "review_scores_location",
  "review_scores_value"
]

for c in imputeCols:
  doublesDF = doublesDF.withColumn(c + "_na", when(col(c).isNull(), 1.0).otherwise(0.0))
  
# the for loop will create an column and add a default value of 1 if the value is NA. This makes sense since there probably is altleast 1 bedroom at a place.
# it does this for all the specifided columns

In [0]:
## creating additional features

from pyspark.ml.feature import Imputer
# below I am creating an estimator called imputer, I'm finding the median of the inputcols and then I'm going to output the imputecols
imputer = Imputer(strategy="median", inputCols=imputeCols, outputCols=imputeCols)

imputerModel = imputer.fit(doublesDF) # this is an estimator
# compute the median for all the input columns using doublesDF


imputedDF = imputerModel.transform(doublesDF)

display(imputedDF)



host_is_superhost host_response_time host_response_rate host_acceptance_rate host_total_listings_count neighbourhood_cleansed latitude longitude room_type accommodates bedrooms beds minimum_nights availability_30 availability_60 availability_90 availability_365 number_of_reviews review_scores_rating review_scores_accuracy review_scores_cleanliness review_scores_checkin review_scores_communication review_scores_location review_scores_value reviews_per_month price bathrooms bedrooms_na bathrooms_na beds_na review_scores_rating_na review_scores_accuracy_na review_scores_cleanliness_na review_scores_checkin_na review_scores_communication_na review_scores_location_na review_scores_value_na f within a few hours 1.0 1.0 1.0 Saint Andrews 45.13241 -67.04725 Entire home/apt 6.0 2.0 5.0 2.0 5.0 16.0 40.0 315.0 21.0 4.67 4.71 4.57 5.0 4.86 4.9 4.62 0.97 242.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 f within a day 1.0 0.33 1.0 Dundas 46.32857 -64.52445 Entire home/apt 5.0 3.0 3.0 7.0 0.0 0.0 17.0 292.0 8.0 5.0 4.88 5.0 4.86 4.71 5.0 4.71 0.11 125.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 f within a few hours 1.0 1.0 2.0 City of Saint John 45.27727 -66.0604 Entire home/apt 4.0 2.0 5.0 2.0 0.0 0.0 17.0 292.0 44.0 4.59 4.68 4.77 4.68 4.84 4.68 4.73 1.27 103.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 f within a few hours 1.0 0.67 1.0 Sackville 45.894821 -64.376556 Private room 2.0 1.0 1.0 1.0 2.0 5.0 26.0 275.0 52.0 4.77 4.9 4.81 4.88 4.92 4.92 4.82 0.53 69.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 f N/A null 0.0 1.0 Shippagan 47.86785 -64.52187 Entire home/apt 6.0 2.0 2.0 7.0 0.0 0.0 0.0 261.0 3.0 4.67 3.67 4.67 4.67 4.67 4.67 4.33 0.13 135.0 1.5 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 f within a day 0.67 null 1.0 Cambridge 45.85825 -66.11696 Entire home/apt 2.0 2.0 1.0 7.0 23.0 53.0 83.0 358.0 0.0 4.92 4.96 4.95 5.0 5.0 4.94 4.9 null 130.0 1.0 0.0 0.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 1.0 t within an hour 1.0 0.97 3.0 Moncton 46.10555 -64.81432 Entire home/apt 7.0 3.0 4.0 3.0 7.0 22.0 49.0 323.0 192.0 4.88 4.92 4.86 4.94 4.95 4.79 4.86 2.27 138.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 f within a day 1.0 1.0 8.0 City of Saint John 45.27233 -66.05694 Private room 2.0 1.0 1.0 1.0 25.0 55.0 85.0 360.0 126.0 4.58 4.63 4.83 4.65 4.67 4.67 4.64 1.71 145.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 f within a day 1.0 1.0 0.0 Gagetown 45.78008 -66.14374 Entire home/apt 2.0 1.0 1.0 2.0 17.0 47.0 77.0 77.0 1.0 5.0 5.0 5.0 5.0 5.0 5.0 5.0 1.0 215.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 t within a day 0.95 0.83 10.0 City of Saint John 45.27358 -66.05307 Private room 2.0 1.0 1.0 1.0 0.0 0.0 0.0 80.0 39.0 4.84 4.95 4.79 4.89 4.92 4.82 4.84 0.54 125.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 t within an hour 1.0 1.0 1.0 Bright 45.97722 -66.84614 Entire home/apt 4.0 2.0 3.0 3.0 0.0 8.0 19.0 283.0 134.0 4.72 4.89 4.92 4.91 4.92 4.62 4.78 1.82 139.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 f within a day 1.0 1.0 8.0 City of Saint John 45.27406 -66.05772 Private room 2.0 2.0 1.0 1.0 26.0 56.0 86.0 361.0 70.0 4.71 4.78 4.81 4.88 4.86 4.81 4.76 1.41 159.0 1.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 f within a few hours 1.0 0.95 4.0 Springfield 45.64933 -65.8593 Private room 16.0 9.0 10.0 1.0 10.0 28.0 55.0 330.0 63.0 4.7 4.82 4.69 4.89 4.92 4.73 4.82 1.04 35.0 3.5 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 f N/A null null 1.0 Richibucto 46.68234 -64.80627 Entire home/apt 5.0 2.0 3.0 2.0 1.0 18.0 48.0 173.0 103.0 4.76 4.86 4.45 4.96 4.97 4.84 4.72 1.41 150.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 f within a few hours 1.0 0.95 4.0 Springfield 45.64943 -65.86004 Private room 16.0 9.0 9.0 1.0 10.0 28.0 55.0 330.0 131.0 4.71 4.85 4.66 4.86 4.88 4.7 4.81 1.55 35.0 3.5 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 f N/A null 0.67 1.0 Kingston 45.44755 -66.00487 Entire home/apt 8.0 4.0 5.0 7.0 1.0 1.0 1.0 1.0 44.0 4.45 4.62 4.42 4.77 4.59 4.84 4.48 0.91 150.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 t N/A null 1.0 3.0 Hillsborough 45.94133 -64.

In [0]:
display(imputedDF.describe())

summary host_is_superhost host_response_time host_response_rate host_acceptance_rate host_total_listings_count neighbourhood_cleansed latitude longitude room_type accommodates bedrooms beds minimum_nights availability_30 availability_60 availability_90 availability_365 number_of_reviews review_scores_rating review_scores_accuracy review_scores_cleanliness review_scores_checkin review_scores_communication review_scores_location review_scores_value reviews_per_month price bathrooms bedrooms_na bathrooms_na beds_na review_scores_rating_na review_scores_accuracy_na review_scores_cleanliness_na review_scores_checkin_na review_scores_communication_na review_scores_location_na review_scores_value_na count 2030 2030 1781 1818 2030 2031 2031 2031 2031 2031 2031 2031 2031 2031 2031 2031 2031 2031 2031 2031 2031 2031 2031 2031 2031 1706 2031 2031 2031 2031 2031 2031 2031 2031 2031 2031 2031 2031 mean null null 0.9577765300393055 0.8846039603960444 3.7635467980295565 null 46.12466723800722 -65.61208962168683 null 4.4362383062530775 1.967503692762186 2.535696701132447 2.7346134908911868 7.182176267848351 21.492368291482027 41.493353028064995 197.49532250123093 26.193008370260955 4.823210241260469 4.8814574101427155 4.858714918759264 4.937872968980787 4.929423929098955 4.882304283604141 4.815800098473607 1.8381535756154734 150.70556376169375 1.2306745445593303 0.055145248645987195 0.0054160512063023145 0.007385524372230428 0.16001969473165928 0.1634662727720335 0.1634662727720335 0.1634662727720335 0.1634662727720335 0.1634662727720335 0.1634662727720335 stddev null null 0.16984890023054514 0.2142280363113545 7.5909631645741245 null 0.743759459338508 1.0570769641185573 null 2.5163008329884593 1.1150239661923873 1.7760256162955206 5.133870752391538 8.971673945792054 17.834372520673842 26.683084993334568 120.24310290342716 45.68919599747835 0.41587954704308244 0.27985806225276166 0.3133621474227856 0.19780770284153978 0.23653557205172202 0.23906964167952122 0.3275172126037265 2.763525807340625 139.8692209847526 0.5858255830287811 0.22831976987568023 0.07341233650483316 0.08564221926939687 0.36671461045785525 0.3698816196188513 0.3698816196188513 0.3698816196188513 0.3698816196188513 0.3698816196188513 0.3698816196188513 min f N/A 0.0 0.0 0.0 Aberdeen 44.61924 -68.73899 Entire home/apt 1.0 1.0 0.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 0.02 13.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 max t within an hour 1.0 1.0 44.0 Woodstock 48.06377 -63.77647 Shared room 16.0 9.0 16.0 182.0 30.0 60.0 90.0 365.0 428.0 5.0 5.0 5.0 5.0 5.0 5.0 5.0 41.0 3500.0 7.0 1.0 1.0 1.0 1.0 1.0 1.0 1.0 1.0 1.0 1.0

In [0]:
# I think I have completed the imputed steps correctly based upon an example I followed. Let's save the data to the delta lake

## This is the O.G. code I used to write to the delta lake
deltaPath = "/delta/nb_airbnb" 

imputedDF.write.format("delta").save(deltaPath)
spark.sql("CREATE TABLE cleaned_nb USING DELTA LOCATION '/delta/nb_airbnb'") # I can now access this table in the data tab, then click default


# If I ever wanted to drop this delta table: dbutils.fs.rm('/tmp/delta-table',recurse=True)

--------------------------------------------------------------------------- 
 NameError Traceback (most recent call last)
 <command-4270216185741124> in <module> 
 4 deltaPath = "/delta/nb_airbnb" 
 5 
 ----> 6 imputedDF . write . format ( "delta" ) . save ( deltaPath ) 
 7 spark . sql ( "CREATE TABLE cleaned_nb USING DELTA LOCATION '/delta/nb_airbnb'" ) # I can now access this table in the data tab, then click default 
 8 

 NameError : name 'imputedDF' is not defined

In [0]:
deltaPath = "/delta/nb_airbnb"
cleaned_nb = spark.read.format("delta").load(deltaPath)
display(cleaned_nb)

## sweet looks like it worked!

In [0]:
# last thing: lets replace "N/A" in host_response_time with "null" and practice updating the delta lake table with the new change

from pyspark.sql.functions import regexp_replace

clean_nb = (cleaned_nb.withColumn("host_response_time", when(col("host_response_time").isin('N/A'), None).otherwise(col("host_response_time")))
            )

display(clean_nb)


In [0]:
clean_nb.write.format("delta").mode("overwrite").save(deltaPath) # lets update the table 

In [0]:
%sql
-- lets look at the history of my delta lake table 

DESCRIBE HISTORY  cleaned_nb

-- pretty dope stuff! 

com.databricks.backend.common.rpc.DatabricksExceptions$SQLExecutionException: org.apache.spark.sql.catalyst.analysis.NoSuchTableException: Table or view 'cleaned_nb' not found in database 'default'
	at org.apache.spark.sql.hive.client.HiveClient.$anonfun$getTable$1(HiveClient.scala:90)
	at scala.Option.getOrElse(Option.scala:189)
	at org.apache.spark.sql.hive.client.HiveClient.getTable(HiveClient.scala:90)
	at org.apache.spark.sql.hive.client.HiveClient.getTable$(HiveClient.scala:89)
	at org.apache.spark.sql.hive.client.PoolingHiveClient.getTable(PoolingHiveClient.scala:42)
	at org.apache.spark.sql.hive.HiveExternalCatalog.$anonfun$getRawTable$1(HiveExternalCatalog.scala:186)
	at com.databricks.spark.util.FrameProfiler$.record(FrameProfiler.scala:80)
	at org.apache.spark.sql.hive.HiveExternalCatalog.$anonfun$withClient$2(HiveExternalCatalog.scala:151)
	at org.apache.spark.sql.hive.HiveExternalCatalog.maybeSynchronized(HiveExternalCatalog.scala:112)
	at org.apache.spark.sql.hive.HiveExternalCatalog.$anonfun$withClient$1(HiveExternalCatalog.scala:150)
	at com.databricks.backend.daemon.driver.ProgressReporter$.withStatusCode(ProgressReporter.scala:377)
	at com.databricks.backend.daemon.driver.ProgressReporter$.withStatusCode(ProgressReporter.scala:363)
	at com.databricks.spark.util.SparkDatabricksProgressReporter$.withStatusCode(ProgressReporter.scala:34)
	at org.apache.spark.sql.hive.HiveExternalCatalog.withClient(HiveExternalCatalog.scala:149)
	at org.apache.spark.sql.hive.HiveExternalCatalog.getRawTable(HiveExternalCatalog.scala:186)
	at org.apache.spark.sql.hive.HiveExternalCatalog.$anonfun$getTable$1(HiveExternalCatalog.scala:818)
	at com.databricks.spark.util.FrameProfiler$.record(FrameProfiler.scala:80)
	at org.apache.spark.sql.hive.HiveExternalCatalog.$anonfun$withClient$2(HiveExternalCatalog.scala:151)
	at org.apache.spark.sql.hive.HiveExternalCatalog.maybeSynchronized(HiveExternalCatalog.scala:112)
	at org.apache.spark.sql.hive.HiveExternalCatalog.$anonfun$withClient$1(HiveExternalCatalog.scala:150)
	at com.databricks.backend.daemon.driver.ProgressReporter$.withStatusCode(ProgressReporter.scala:377)
	at com.databricks.backend.daemon.driver.ProgressReporter$.withStatusCode(ProgressReporter.scala:363)
	at com.databricks.spark.util.SparkDatabricksProgressReporter$.withStatusCode(ProgressReporter.scala:34)
	at org.apache.spark.sql.hive.HiveExternalCatalog.withClient(HiveExternalCatalog.scala:149)
	at org.apache.spark.sql.hive.HiveExternalCatalog.getTable(HiveExternalCatalog.scala:818)
	at org.apache.spark.sql.catalyst.catalog.ExternalCatalogWithListener.getTable(ExternalCatalogWithListener.scala:146)
	at org.apache.spark.sql.catalyst.catalog.SessionCatalogImpl.getTableRawMetadata(SessionCatalog.scala:865)
	at com.databricks.sql.managedcatalog.ManagedCatalogSessionCatalog.getTableRawMetadata(ManagedCatalogSessionCatalog.scala:493)
	at com.databricks.sql.DatabricksSessionCatalog.getTableRawMetadata(DatabricksSessionCatalog.scala:83)
	at com.databricks.sql.DatabricksSessionCatalog.getTableMetadata(DatabricksSessionCatalog.scala:89)
	at com.databricks.sql.transaction.tahoe.commands.DescribeDeltaHistoryCommand.metadata$lzycompute$1(DescribeDeltaHistoryCommand.scala:69)
	at com.databricks.sql.transaction.tahoe.commands.DescribeDeltaHistoryCommand.metadata$1(DescribeDeltaHistoryCommand.scala:69)
	at com.databricks.sql.transaction.tahoe.commands.DescribeDeltaHistoryCommand.$anonfun$run$1(DescribeDeltaHistoryCommand.scala:77)
	at com.databricks.sql.acl.CheckPermissions$.trusted(CheckPermissions.scala:1325)
	at com.databricks.sql.transaction.tahoe.commands.DescribeDeltaHistoryCommand.run(DescribeDeltaHistoryCommand.scala:63)
	at org.apache.spark.sql.execution.command.ExecutedCommandExec.sideEffectResult$lzycompute(commands.scala:75)
	at org.apache.spark.sql.execution.command.ExecutedCommandExec.sideEffectResult(commands.scala:73)
	at org.apache.spark.sql.execution.command.ExecutedCommandExec.executeCollect(commands.scala:84)
	at org.

In [0]:
# What If I realized I made a mistake in the first version? Delta lake has a cool feature to help me get version zero called "time travel"
deltaPath = "/delta/nb_airbnb"
df = spark.read.format("delta").option("versionAsOf", 0).load(deltaPath) # versionASOF helps me to get the O.G. dataset from the above cell. 
display(df)


## super cool!!!!

host_is_superhost host_response_time host_response_rate host_acceptance_rate host_total_listings_count neighbourhood_cleansed latitude longitude room_type accommodates bedrooms beds minimum_nights availability_30 availability_60 availability_90 availability_365 number_of_reviews review_scores_rating review_scores_accuracy review_scores_cleanliness review_scores_checkin review_scores_communication review_scores_location review_scores_value reviews_per_month price bathrooms bedrooms_na bathrooms_na beds_na review_scores_rating_na review_scores_accuracy_na review_scores_cleanliness_na review_scores_checkin_na review_scores_communication_na review_scores_location_na review_scores_value_na f within a few hours 1.0 1.0 1.0 Saint Andrews 45.13241 -67.04725 Entire home/apt 6.0 2.0 5.0 2.0 5.0 16.0 40.0 315.0 21.0 4.67 4.71 4.57 5.0 4.86 4.9 4.62 0.97 242.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 f within a day 1.0 0.33 1.0 Dundas 46.32857 -64.52445 Entire home/apt 5.0 3.0 3.0 7.0 0.0 0.0 17.0 292.0 8.0 5.0 4.88 5.0 4.86 4.71 5.0 4.71 0.11 125.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 f within a few hours 1.0 1.0 2.0 City of Saint John 45.27727 -66.0604 Entire home/apt 4.0 2.0 5.0 2.0 0.0 0.0 17.0 292.0 44.0 4.59 4.68 4.77 4.68 4.84 4.68 4.73 1.27 103.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 f within a few hours 1.0 0.67 1.0 Sackville 45.894821 -64.376556 Private room 2.0 1.0 1.0 1.0 2.0 5.0 26.0 275.0 52.0 4.77 4.9 4.81 4.88 4.92 4.92 4.82 0.53 69.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 f N/A null 0.0 1.0 Shippagan 47.86785 -64.52187 Entire home/apt 6.0 2.0 2.0 7.0 0.0 0.0 0.0 261.0 3.0 4.67 3.67 4.67 4.67 4.67 4.67 4.33 0.13 135.0 1.5 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 f within a day 0.67 null 1.0 Cambridge 45.85825 -66.11696 Entire home/apt 2.0 2.0 1.0 7.0 23.0 53.0 83.0 358.0 0.0 4.92 4.96 4.95 5.0 5.0 4.94 4.9 null 130.0 1.0 0.0 0.0 0.0 1.0 1.0 1.0 1.0 1.0 1.0 1.0 t within an hour 1.0 0.97 3.0 Moncton 46.10555 -64.81432 Entire home/apt 7.0 3.0 4.0 3.0 7.0 22.0 49.0 323.0 192.0 4.88 4.92 4.86 4.94 4.95 4.79 4.86 2.27 138.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 f within a day 1.0 1.0 8.0 City of Saint John 45.27233 -66.05694 Private room 2.0 1.0 1.0 1.0 25.0 55.0 85.0 360.0 126.0 4.58 4.63 4.83 4.65 4.67 4.67 4.64 1.71 145.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 f within a day 1.0 1.0 0.0 Gagetown 45.78008 -66.14374 Entire home/apt 2.0 1.0 1.0 2.0 17.0 47.0 77.0 77.0 1.0 5.0 5.0 5.0 5.0 5.0 5.0 5.0 1.0 215.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 t within a day 0.95 0.83 10.0 City of Saint John 45.27358 -66.05307 Private room 2.0 1.0 1.0 1.0 0.0 0.0 0.0 80.0 39.0 4.84 4.95 4.79 4.89 4.92 4.82 4.84 0.54 125.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 t within an hour 1.0 1.0 1.0 Bright 45.97722 -66.84614 Entire home/apt 4.0 2.0 3.0 3.0 0.0 8.0 19.0 283.0 134.0 4.72 4.89 4.92 4.91 4.92 4.62 4.78 1.82 139.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 f within a day 1.0 1.0 8.0 City of Saint John 45.27406 -66.05772 Private room 2.0 2.0 1.0 1.0 26.0 56.0 86.0 361.0 70.0 4.71 4.78 4.81 4.88 4.86 4.81 4.76 1.41 159.0 1.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 f within a few hours 1.0 0.95 4.0 Springfield 45.64933 -65.8593 Private room 16.0 9.0 10.0 1.0 10.0 28.0 55.0 330.0 63.0 4.7 4.82 4.69 4.89 4.92 4.73 4.82 1.04 35.0 3.5 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 f N/A null null 1.0 Richibucto 46.68234 -64.80627 Entire home/apt 5.0 2.0 3.0 2.0 1.0 18.0 48.0 173.0 103.0 4.76 4.86 4.45 4.96 4.97 4.84 4.72 1.41 150.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 f within a few hours 1.0 0.95 4.0 Springfield 45.64943 -65.86004 Private room 16.0 9.0 9.0 1.0 10.0 28.0 55.0 330.0 131.0 4.71 4.85 4.66 4.86 4.88 4.7 4.81 1.55 35.0 3.5 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 f N/A null 0.67 1.0 Kingston 45.44755 -66.00487 Entire home/apt 8.0 4.0 5.0 7.0 1.0 1.0 1.0 1.0 44.0 4.45 4.62 4.42 4.77 4.59 4.84 4.48 0.91 150.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 t N/A null 1.0 3.0 Hillsborough 45.94133 -64.

### Note: its important to know that delta lake tables are saved on the cluster you use, but it seems that in the community version the detla table is still available even with the creation and use of a new cluster. 

### Note: there are still null values in the data set, so it is up to you to drop the null values or change them.